<a href="https://colab.research.google.com/github/YashwanthRaasa/Capstone-project/blob/main/Capstone_project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import pandas as pd

# Load the dataset
df = pd.read_csv("dataset.csv")

# Show first 5 rows
df.head()


ID SystemCodeNumber  Capacity   Latitude  Longitude  Occupancy VehicleType  \
0   0      BHMBCCMKT01       577  26.144536  91.736172       61.0         car   
1   1      BHMBCCMKT01       577  26.144536  91.736172       64.0         car   
2   2      BHMBCCMKT01       577  26.144536  91.736172       80.0         car   
3   3      BHMBCCMKT01       577  26.144536  91.736172      107.0         car   
4   4      BHMBCCMKT01       577  26.144536  91.736172      150.0        bike   

  TrafficConditionNearby  QueueLength  IsSpecialDay LastUpdatedDate  \
0                    low          1.0           0.0      04-10-2016   
1                    low          1.0           0.0      04-10-2016   
2                    low          2.0           0.0      04-10-2016   
3                    low          2.0           0.0      04-10-2016   
4                    low          2.0           0.0      04-10-2016   

  LastUpdatedTime  
0        07:59:00  
1        08:25:00  
2        08:59:00  
3        09:32:00  
4        09:59:00

In [2]:
# Load your dataset
df.columns

Index(['ID', 'SystemCodeNumber', 'Capacity', 'Latitude', 'Longitude',
       'Occupancy', 'VehicleType', 'TrafficConditionNearby', 'QueueLength',
       'IsSpecialDay', 'LastUpdatedDate', 'LastUpdatedTime'],
      dtype='object')

In [3]:
# Set base price and alpha
BASE_PRICE = 10
ALPHA = 5

# Model 1: Price increases linearly with occupancy
df['Model1_Price'] = BASE_PRICE + ALPHA * (df['Occupancy'] / df['Capacity'])

# Show result
df[['Occupancy', 'Capacity', 'Model1_Price']].head()

Occupancy  Capacity  Model1_Price
0       61.0       577     10.528596
1       64.0       577     10.554593
2       80.0       577     10.693241
3      107.0       577     10.927210
4      150.0       577     11.299827

In [4]:
# Model 2 – Demand-Based Pricing
# Encode vehicle type (weights)
vehicle_weights = {
    'car': 1.0,
    'bike': 0.5,
    'truck': 1.5
}

# Add weight column
df['VehicleTypeWeight'] = df['VehicleType'].map(vehicle_weights)



In [5]:
# Encode TrafficConditionNearby
traffic_mapping = {
    'low': 1,
    'average': 2,
    'high': 3
}

df['TrafficLevel'] = df['TrafficConditionNearby'].map(traffic_mapping)

In [6]:
df[['TrafficConditionNearby', 'TrafficLevel']]


TrafficConditionNearby  TrafficLevel
0                        low           1.0
1                        low           1.0
2                        low           1.0
3                        low           1.0
4                        low           1.0
...                      ...           ...
12203                    low           1.0
12204                    low           1.0
12205                    low           1.0
12206                    low           1.0
12207                    NaN           NaN

[12208 rows x 2 columns]

In [7]:
# Set coefficients (you can tune these)
alpha = 2
beta = 1.5
gamma = 1.2
delta = 1.0
epsilon = 1.0
lambd = 0.5  # λ for price scaling

# Raw demand formula
df['RawDemand'] = (
    alpha * (df['Occupancy'] / df['Capacity']) +
    beta * df['QueueLength'] -
    gamma * df['TrafficLevel'] +
    delta * df['IsSpecialDay'] +
    epsilon * df['VehicleTypeWeight']
)

# Normalize Demand to 0-1 (min-max scaling)
dmin = df['RawDemand'].min()
dmax = df['RawDemand'].max()
df['NormalizedDemand'] = (df['RawDemand'] - dmin) / (dmax - dmin)

# Calculate price using demand
df['Model2_Price'] = BASE_PRICE * (1 + lambd * df['NormalizedDemand'])

# Clamp price between 0.5x and 2x base price
df['Model2_Price'] = df['Model2_Price'].clip(lower=BASE_PRICE * 0.5, upper=BASE_PRICE * 2.0)

# Show results
df[['Occupancy', 'QueueLength', 'TrafficLevel', 'VehicleType', 'Model2_Price']].head()


Occupancy  QueueLength  TrafficLevel VehicleType  Model2_Price
0       61.0          1.0           1.0         car     10.517295
1       64.0          1.0           1.0         car     10.519770
2       80.0          2.0           1.0         car     10.890003
3      107.0          2.0           1.0         car     10.912278
4      150.0          2.0           1.0        bike     10.828744

In [8]:
df.columns


Index(['ID', 'SystemCodeNumber', 'Capacity', 'Latitude', 'Longitude',
       'Occupancy', 'VehicleType', 'TrafficConditionNearby', 'QueueLength',
       'IsSpecialDay', 'LastUpdatedDate', 'LastUpdatedTime', 'Model1_Price',
       'VehicleTypeWeight', 'TrafficLevel', 'RawDemand', 'NormalizedDemand',
       'Model2_Price'],
      dtype='object')

In [9]:
!pip install bokeh --quiet


In [10]:
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource
from bokeh.layouts import column
import pandas as pd

output_notebook()

# Sort by Occupancy for cleaner curves
df_sorted = df.sort_values(by='Occupancy').reset_index(drop=True)

# Smoothing using rolling mean (window size = 50, tune as needed)
df_sorted['Model1_Price_Smooth'] = df_sorted['Model1_Price'].rolling(window=50, min_periods=1).mean()
df_sorted['Model2_Price_Smooth'] = df_sorted['Model2_Price'].rolling(window=50, min_periods=1).mean()

# Data source
source = ColumnDataSource(data={
    'Occupancy': df_sorted['Occupancy'],
    'Model1_Price': df_sorted['Model1_Price_Smooth'],
    'Model2_Price': df_sorted['Model2_Price_Smooth']
})

# Create Bokeh figure
p = figure(title="Dynamic Pricing Comparison (Smoothed + Transparent)",
           x_axis_label="Occupancy",
           y_axis_label="Price ($)",
           width=800, height=400)

# Add lines with smoothing + transparency
p.line('Occupancy', 'Model1_Price', source=source, legend_label="Model 1: Linear",
       line_width=2, color='blue', alpha=0.6)

p.line('Occupancy', 'Model2_Price', source=source, legend_label="Model 2: Demand-Based",
       line_width=2, color='green', alpha=0.4)

# Style
p.legend.location = "top_left"
p.grid.grid_line_alpha = 0.3

# Show plot
show(p)


In [11]:
# Create a fake Time and LotID column for simulation
df['Time'] = pd.date_range(start='2025-01-01 08:00', periods=len(df), freq='30T')
df['LotID'] = 'Lot_A'  # You can randomize this for multiple lots

# Filter for one lot
lot_df = df[df['LotID'] == 'Lot_A'].copy()
lot_df = lot_df.sort_values(by='Time').reset_index(drop=True)


/tmp/ipython-input-11-2558410533.py:2: FutureWarning: 'T' is deprecated and will be removed in a future version, please use 'min' instead.
  df['Time'] = pd.date_range(start='2025-01-01 08:00', periods=len(df), freq='30T')


In [12]:
source = ColumnDataSource(data={'Time': [], 'Price': []})

p = figure(title="Real-Time Price Updates for Lot A",
           x_axis_type='datetime', width=800, height=400)
p.line(x='Time', y='Price', source=source, line_width=2, color='blue', legend_label="Model 2 Price")

handle = show(p, notebook_handle=True)


In [13]:
import pandas as pd
# Simulate a time column (30-minute intervals)
df['Time'] = pd.date_range(start='2025-01-01 08:00', periods=len(df), freq='30min')

# Simulate a single parking lot
df['LotID'] = 'Lot_A'


In [14]:
# Filter for one lot and sort by time
lot_df = df[df['LotID'] == 'Lot_A'].sort_values(by='Time').reset_index(drop=True)


In [15]:
from bokeh.models import ColumnDataSource

output_notebook()

source = ColumnDataSource(lot_df)

p = figure(title="Model 2 Price Over Time – Lot A",
           x_axis_type='datetime',
           x_axis_label="Time",
           y_axis_label="Model 2 Price ($)",
           width=800, height=400)

p.line(x='Time', y='Model2_Price', source=source, line_width=2, color='green', legend_label="Lot A")


show(p)


In [16]:
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource

output_notebook()

# Optional: smooth Model 1 price
lot_df['Smooth_Model1'] = lot_df['Model1_Price'].rolling(window=20, min_periods=1).mean()

source = ColumnDataSource(lot_df)

p = figure(title="Model 1 Price Over Time – Lot A",
           x_axis_type='datetime',
           x_axis_label="Time",
           y_axis_label="Model 1 Price ($)",
           width=800, height=400)

p.line(x='Time', y='Smooth_Model1', source=source, line_width=2, color='blue', legend_label="Lot A")

show(p)


In [17]:
!pip install pathway --quiet
import pathway as pw


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.4/60.4 kB 5.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 149.4/149.4 kB 12.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 69.7/69.7 MB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 77.6/77.6 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 777.6/777.6 kB 41.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.2/139.2 kB 13.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 26.5/26.5 MB 69.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 135.3/135.3 kB 9.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 244.6/244.6 kB 15.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 318.4/318.4 kB 24.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 985.8/985.8 kB 52.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [18]:
# Define a Schema for the CSV
['Occupancy', 'Capacity', 'QueueLength', 'TrafficConditionNearby', 'IsSpecialDay', 'VehicleType']


['Occupancy',
 'Capacity',
 'QueueLength',
 'TrafficConditionNearby',
 'IsSpecialDay',
 'VehicleType']

In [19]:
class ParkingSchema(pw.Schema):
    Occupancy: int
    Capacity: int
    QueueLength: int
    TrafficConditionNearby: str
    IsSpecialDay: int
    VehicleType: str


In [20]:
# Define Mapping Functions First
# We'll reuse your Model 2 demand function, but in pure Python:
@pw.udf
def calculate_model2_price(occupancy, capacity, queue, traffic, is_special, vehicle_type):
    # Map traffic
    traffic_map = {'low': 1, 'average': 2, 'high': 3}
    vehicle_map = {'car': 1.0, 'bike': 0.5, 'truck': 1.5}

    traffic_level = traffic_map.get(traffic.lower(), 2)
    vehicle_weight = vehicle_map.get(vehicle_type.lower(), 1.0)

    # Demand formula
    alpha = 2
    beta = 1.5
    gamma = 1.2
    delta = 1.0
    epsilon = 1.0
    lambd = 0.5
    base_price = 10

    raw_demand = (
        alpha * (occupancy / capacity) +
        beta * queue -
        gamma * traffic_level +
        delta * is_special +
        epsilon * vehicle_weight
    )

    # Normalize (skip scaling step for simplicity here)
    demand = max(0, min(raw_demand / 10, 1))  # Simple bounded normalization

    price = base_price * (1 + lambd * demand)
    return min(max(price, base_price * 0.5), base_price * 2.0)


In [64]:
# Build the Pathway Pipeline
input_table = pw.io.csv.read("dataset.csv", schema=ParkingSchema,mode="static")

result_table = input_table.select(
    Occupancy=input_table.Occupancy,
    Capacity=input_table.Capacity,
    QueueLength=input_table.QueueLength,
    Traffic=input_table.TrafficConditionNearby,
    Vehicle=input_table.VehicleType,
    IsSpecial=input_table.IsSpecialDay,
    Model2_Price=calculate_model2_price(
        input_table.Occupancy,
        input_table.Capacity,
        input_table.QueueLength,
        input_table.TrafficConditionNearby,
        input_table.IsSpecialDay,
        input_table.VehicleType
    )
)


In [65]:
output_table = result_table  # or rename if needed




In [66]:
pw.io.csv.write(
    table=result_table,
    filename="model2_output.csv"
)



In [68]:
pw.run()


Output()

KeyboardInterrupt: 

In [69]:
import pandas as pd

df = pd.read_csv("model2_output.csv")
df.head()


Occupancy  Capacity  QueueLength  Traffic Vehicle  IsSpecial  Model2_Price  \
0        558       687            6  average   truck          1     15.000000   
1       1293      3103            8     high    bike          0     14.866694   
2        732      2937           11     high   truck          1     15.000000   
3       1103      2937            4      low   truck          0     13.525553   
4       3104      3883           10     high   truck          0     15.000000   

            time  diff  
0  1751819852150     1  
1  1751819852150     1  
2  1751819852150     1  
3  1751819852150     1  
4  1751819852150     1

In [71]:
# Model1_Price = BasePrice + α * (Occupancy / Capacity)



In [72]:
@pw.udf
def calculate_model1_price(occupancy, capacity):
    base_price = 10
    alpha = 5
    return base_price + alpha * (occupancy / capacity)


In [73]:
result_table = input_table.select(
    Occupancy=input_table.Occupancy,
    Capacity=input_table.Capacity,
    QueueLength=input_table.QueueLength,
    Traffic=input_table.TrafficConditionNearby,
    Vehicle=input_table.VehicleType,
    IsSpecial=input_table.IsSpecialDay,
    Model1_Price=calculate_model1_price(
        input_table.Occupancy,
        input_table.Capacity
    ),
    Model2_Price=calculate_model2_price(
        input_table.Occupancy,
        input_table.Capacity,
        input_table.QueueLength,
        input_table.TrafficConditionNearby,
        input_table.IsSpecialDay,
        input_table.VehicleType
    )
)


In [76]:
pw.io.csv.write(
    table=result_table,
    filename="final_output.csv"
)


In [88]:
pw.run()


Output()

KeyboardInterrupt: 

In [78]:
import pandas as pd

df = pd.read_csv("final_output.csv")
df[['Occupancy', 'Capacity', 'Model1_Price', 'Model2_Price']].head()


Occupancy  Capacity  Model1_Price  Model2_Price
0        558       687     14.061135     15.000000
1       1293      3103     12.083468     14.866694
2        732      2937     11.246170     15.000000
3       1103      2937     11.877766     13.525553
4       3104      3883     13.996910     15.000000